In [1]:
# Check Environment

import sys
print(sys.version)
print(sys.executable)

3.7.5 (default, Oct 31 2019, 15:18:51) [MSC v.1916 64 bit (AMD64)]
C:\Users\Dennis\anaconda3\envs\rc_env_np16p6_dnntest\python.exe


In [2]:
# IMPORTS

import rescomp
import numpy as np

import pandas as pd

import plotly.express as px

import matplotlib.pyplot as plt
# from mpl_toolkits import mplot3d

### Create Lorenz Dataset:

In [3]:
simulation_time_steps = 8000
dt = 2e-2

starting_point = np.array([-14.03020521, -20.88693127, 25.53545])
sim_data = rescomp.simulate_trajectory(
    sys_flag='lorenz', dt=dt, time_steps=simulation_time_steps,
    starting_point=starting_point)

### Create artificially "wrong" model and plot real and "fake" Lorenz Attractor:

In [4]:
#Create artificially "wrong" model by changing the system parameters:
eps1 = 0.0
eps2 = 0.0
eps3 = 0.0
model = lambda x: rescomp.simulations._normal_lorenz(x, sigma=10*(1+eps1), rho=28*(1+eps2), beta=8/3*(1+eps3))
# model = lambda x: -x

# model_pred = lambda x: x + model(x)*dt
model_pred = lambda x: rescomp.simulations._runge_kutta(model, dt, x)

# test it:
x = np.zeros((simulation_time_steps, 3))

x[0] = starting_point
for i in range(1, simulation_time_steps):
    x_i = x[i-1]
    x[i] = model_pred(x_i)


# Plotly
sim_data_df = pd.DataFrame(data=sim_data, columns = ["x", "y", "z"])
sim_data_df["name"] = "true"
wrong_model_data_df = pd.DataFrame(data=x, columns = ["x", "y", "z"])
wrong_model_data_df["name"] = "wrong"
df = pd.concat([sim_data_df, wrong_model_data_df])
fig = px.line_3d(df, x = "x", y ="y", z="z", color = "name")
fig.show()


# Matplotlib: 
# fig = plt.figure(figsize=(6, 3), dpi=300)
# ax = fig.add_subplot(111, projection='3d')
# ax.plot(x[:, 0], x[:, 1], x[:, 2],
#         alpha=0.8, color='blue', linewidth = 0.1)
# ax.plot(sim_data[:, 0], sim_data[:, 1], sim_data[:, 2],
#         alpha=0.8, color='red', linewidth = 0.1)
# ax.set_title("Normal Lorenz63 System Simulated")
# ax.set_xlabel('x')
# ax.set_ylabel('y')
# ax.set_zlabel('z')
# plt.show()

### Create "normal" and different Hybrid Models:

In [5]:
n_dim = 1000

ESNs = {}
settings_dict = {}

# The Baseline
np.random.seed(1)
name = "normal"
esn_normal = rescomp.esn.ESNWrapper()
esn_normal.create_network(n_dim = n_dim)
ESNs[name] = esn_normal



# # Hybrid only at output: 
# np.random.seed(1)
# name = "hybrid out"
# esn_hybrid_out = rescomp.esn.ESNHybrid()
# esn_hybrid_out.create_network(n_dim = n_dim)
# add_model_to_output = True
# add_model_to_input = False
# esn_hybrid_out.set_model(model_pred, add_model_to_input = add_model_to_input, add_model_to_output = add_model_to_output)
# ESNs[name] = esn_hybrid_out

# # Hybrid only at input:
# np.random.seed(1)
# name = "hybrid in"
# esn_hybrid_in = rescomp.esn.ESNHybrid()
# esn_hybrid_in.create_network(n_dim = n_dim)
# add_model_to_output = False
# add_model_to_input = True
# gamma = 0.5
# esn_hybrid_in.set_model(model_pred, add_model_to_input = add_model_to_input,
#                         add_model_to_output = add_model_to_output,
#                        gamma = gamma)
# ESNs[name] = esn_hybrid_in

# # Hybrid at in- and output: 
# np.random.seed(1)
# name = "hybrid both"
# esn_hybrid_both = rescomp.esn.ESNHybrid()
# esn_hybrid_both.create_network(n_dim = n_dim)
# add_model_to_output = True
# add_model_to_input = True
# gamma = 0.5
# esn_hybrid_both.set_model(model_pred, add_model_to_input = add_model_to_input,
#                         add_model_to_output = add_model_to_output,
#                        gamma = gamma)
# ESNs[name] = esn_hybrid_both

# The Test
np.random.seed(1)
name = "Dnn"
n_dim = 50
esn_normal = rescomp.esn.ESNDnn()
esn_normal.create_network(n_dim = n_dim, )
ESNs[name] = esn_normal

### Train and predict:

In [6]:
train_sync_steps = 500
train_steps = 6000
pred_steps = 1500 

# For testing different W_in settings
w_in_sparse=True #True
w_in_ordered=True #False
w_in_no_update=False #False
act_fct_flag='tanh_simple' #'tanh_simple'
w_out_fit_flag="simple" #"simple"
reg_param = 1e-10

ESNs_results = {}

for name, ESN in ESNs.items():
    print("---- Training and predicting " + name + " ----")
    
    ESN.train(x_train=sim_data[:train_sync_steps + train_steps], sync_steps=train_sync_steps, reg_param=reg_param, 
             w_in_sparse=w_in_sparse, 
             w_in_ordered=w_in_ordered, w_in_no_update=w_in_no_update, act_fct_flag=act_fct_flag, 
             w_out_fit_flag=w_out_fit_flag)
    
    out = ESN.predict(sim_data[train_sync_steps + train_steps-1:])
    ESNs_results[name] = out


---- Training and predicting normal ----
---- Training and predicting Dnn ----
Building dnn model
Instructions for updating:
Call initializer instance with the dtype argument instead of passing it to the constructor
Model: "sequential"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
dense (Dense)                (None, 256)               13056     
_________________________________________________________________
dense_1 (Dense)              (None, 64)                16448     
_________________________________________________________________
dense_2 (Dense)              (None, 3)                 195       
Total params: 29,699
Trainable params: 29,699
Non-trainable params: 0
_________________________________________________________________
Epoch 1/500
5999/5999 [==============================] - 1s 98us/sample - loss: 9.4763
Epoch 2/500
5999/5999 [==============================] - 0s 58us/sample - loss:

5999/5999 [==============================] - 0s 48us/sample - loss: 0.0888
Epoch 81/500
5999/5999 [==============================] - 0s 49us/sample - loss: 0.0906
Epoch 82/500
5999/5999 [==============================] - 0s 46us/sample - loss: 0.0857
Epoch 83/500
5999/5999 [==============================] - 0s 48us/sample - loss: 0.0845
Epoch 84/500
5999/5999 [==============================] - 0s 47us/sample - loss: 0.0840
Epoch 85/500
5999/5999 [==============================] - 0s 48us/sample - loss: 0.0810
Epoch 86/500
5999/5999 [==============================] - 0s 47us/sample - loss: 0.0830
Epoch 87/500
5999/5999 [==============================] - 0s 45us/sample - loss: 0.0811
Epoch 88/500
5999/5999 [==============================] - 0s 46us/sample - loss: 0.0814
Epoch 89/500
5999/5999 [==============================] - 0s 46us/sample - loss: 0.0798
Epoch 90/500
5999/5999 [==============================] - 0s 47us/sample - loss: 0.0761
Epoch 91/500
5999/5999 [=====================

5999/5999 [==============================] - 0s 47us/sample - loss: 0.0485
Epoch 172/500
5999/5999 [==============================] - 0s 45us/sample - loss: 0.0494
Epoch 173/500
5999/5999 [==============================] - 0s 46us/sample - loss: 0.0474
Epoch 174/500
5999/5999 [==============================] - 0s 45us/sample - loss: 0.0481
Epoch 175/500
5999/5999 [==============================] - 0s 45us/sample - loss: 0.0456
Epoch 176/500
5999/5999 [==============================] - 0s 47us/sample - loss: 0.0508
Epoch 177/500
5999/5999 [==============================] - 0s 45us/sample - loss: 0.0449
Epoch 178/500
5999/5999 [==============================] - 0s 45us/sample - loss: 0.0485
Epoch 179/500
5999/5999 [==============================] - 0s 49us/sample - loss: 0.0488
Epoch 180/500
5999/5999 [==============================] - 0s 46us/sample - loss: 0.0467
Epoch 181/500
5999/5999 [==============================] - 0s 50us/sample - loss: 0.0482
Epoch 182/500
5999/5999 [==========

5999/5999 [==============================] - 0s 62us/sample - loss: 0.0434
Epoch 263/500
5999/5999 [==============================] - 0s 46us/sample - loss: 0.0422
Epoch 264/500
5999/5999 [==============================] - 0s 47us/sample - loss: 0.0401
Epoch 265/500
5999/5999 [==============================] - 0s 50us/sample - loss: 0.0419
Epoch 266/500
5999/5999 [==============================] - 0s 58us/sample - loss: 0.04350s - loss: 0.044
Epoch 267/500
5999/5999 [==============================] - 0s 48us/sample - loss: 0.0393
Epoch 268/500
5999/5999 [==============================] - 0s 46us/sample - loss: 0.0407
Epoch 269/500
5999/5999 [==============================] - 0s 46us/sample - loss: 0.0432
Epoch 270/500
5999/5999 [==============================] - 0s 47us/sample - loss: 0.0411
Epoch 271/500
5999/5999 [==============================] - 0s 47us/sample - loss: 0.0407
Epoch 272/500
5999/5999 [==============================] - 0s 46us/sample - loss: 0.0411
Epoch 273/500
5999/

5999/5999 [==============================] - 0s 46us/sample - loss: 0.0369
Epoch 355/500
5999/5999 [==============================] - 0s 48us/sample - loss: 0.0404
Epoch 356/500
5999/5999 [==============================] - 0s 45us/sample - loss: 0.0383
Epoch 357/500
5999/5999 [==============================] - 0s 44us/sample - loss: 0.0361
Epoch 358/500
5999/5999 [==============================] - 0s 48us/sample - loss: 0.0388
Epoch 359/500
5999/5999 [==============================] - 0s 48us/sample - loss: 0.0382
Epoch 360/500
5999/5999 [==============================] - 0s 45us/sample - loss: 0.03800s - loss: 0.0
Epoch 361/500
5999/5999 [==============================] - 0s 45us/sample - loss: 0.0380
Epoch 362/500
5999/5999 [==============================] - 0s 49us/sample - loss: 0.0379
Epoch 363/500
5999/5999 [==============================] - 0s 45us/sample - loss: 0.0372
Epoch 364/500
5999/5999 [==============================] - 0s 47us/sample - loss: 0.0370
Epoch 365/500
5999/59

5999/5999 [==============================] - 0s 63us/sample - loss: 0.0353
Epoch 446/500
5999/5999 [==============================] - 0s 54us/sample - loss: 0.0352
Epoch 447/500
5999/5999 [==============================] - 0s 54us/sample - loss: 0.0359
Epoch 448/500
5999/5999 [==============================] - 0s 61us/sample - loss: 0.0358
Epoch 449/500
5999/5999 [==============================] - 0s 54us/sample - loss: 0.0350
Epoch 450/500
5999/5999 [==============================] - 0s 48us/sample - loss: 0.0368
Epoch 451/500
5999/5999 [==============================] - 0s 49us/sample - loss: 0.0363
Epoch 452/500
5999/5999 [==============================] - 0s 44us/sample - loss: 0.0359
Epoch 453/500
5999/5999 [==============================] - 0s 41us/sample - loss: 0.0356
Epoch 454/500
5999/5999 [==============================] - 0s 44us/sample - loss: 0.0366
Epoch 455/500
5999/5999 [==============================] - 0s 44us/sample - loss: 0.0353
Epoch 456/500
5999/5999 [==========

### Create Dataframe used for plotting (plotly):

In [7]:
frames = []

get_test = True
for name, result in ESNs_results.items():
    y_pred, y_test = result
    
    if get_test:
        df_test = pd.DataFrame(data=y_test, columns = ["x", "y", "z"])
        df_test["name"] = "test"
        frames.append(df_test)
        get_test = False
    df_pred = pd.DataFrame(data=y_pred, columns = ["x", "y", "z"])
    df_pred["name"] = name + " pred"
    frames.append(df_pred)
        
df = pd.concat(frames)
print(df)

              x          y          z      name
0      1.955340   3.594315   9.957817      test
1      2.315795   4.292259   9.604431      test
2      2.750612   5.135080   9.337862      test
3      3.275032   6.149423   9.183554      test
4      3.906541   7.363522   9.178585      test
...         ...        ...        ...       ...
1495  -9.234106 -14.908816  18.253744  Dnn pred
1496 -10.372861 -16.271860  20.353809  Dnn pred
1497 -11.507048 -17.167604  22.910601  Dnn pred
1498 -12.479975 -17.411896  25.832783  Dnn pred
1499 -13.302442 -17.001860  28.894337  Dnn pred

[4500 rows x 4 columns]


### Plot x coordinate of models: prediction vs test:

In [8]:
fig = px.line(df, y="x", color='name')
fig.show()

### Plot attractor: 

In [9]:
fig = px.line_3d(df,x = "x", y ="y", z="z", color='name')
fig.show()

### Create Dataframe for RMSE:

In [10]:
frames = []

for name, result in ESNs_results.items():
    y_pred, y_test = result
    rmse = rescomp.measures.rmse_over_time(y_pred, y_test)
    df_rmse = pd.DataFrame(data=rmse, columns = ["rmse"])
    df_rmse["name"] = "rmse " + name
    frames.append(df_rmse)
        
df_rmse = pd.concat(frames)
print(df_rmse)

           rmse         name
0      0.000035  rmse normal
1      0.000065  rmse normal
2      0.000050  rmse normal
3      0.000135  rmse normal
4      0.000252  rmse normal
...         ...          ...
1495  15.803042     rmse Dnn
1496  17.734262     rmse Dnn
1497  19.775262     rmse Dnn
1498  21.771475     rmse Dnn
1499  23.717867     rmse Dnn

[3000 rows x 2 columns]


### Plot RMSE:

In [11]:
fig = px.line(df_rmse, y="rmse", color='name')
fig.show()

### Plot the average output weights (if model is added to output):

In [ ]:
def get_info_about_output_weights(esn):
    n_dim = esn._n_dim
    rc_weights = esn._w_out[:, : n_dim]
    model_weights = esn._w_out[:, n_dim:]
    

    
    avg_abs_rc_weight = np.average(np.abs(rc_weights))
    avg_abs_model_weight = np.average(np.abs(model_weights))
    return avg_abs_rc_weight, avg_abs_model_weight

for esn_name in ["hybrid out", "hybrid both"]:
    print("______________")
    print(f"{esn_name}: ")
    esn = ESNs[esn_name]
    avg_abs_rc_weight, avg_abs_model_weight = get_info_about_output_weights(esn)
    print(f"avg_abs_rc_weight: {avg_abs_rc_weight}")
    print(f"avg_abs_model_weight: {avg_abs_model_weight}")

# modify _w_out:
def get_modified_w_out(n_dim, state_dim):
    matrix = np.zeros((state_dim, n_dim))
    print(matrix)
    print(matrix[:, 0])
    for i in range(0,state_dim):
        to_add = np.zeros(state_dim)
        to_add[i] = 1
        matrix[:, n_dim - state_dim +i] = to_add
    return matrix

n_dim = 5
state_dim = 3
get_modified_w_out(n_dim, state_dim)

-----------------------------------
# OLD

In [ ]:
# print(esn_hybrid._w_out.shape)
# print(esn_normal._w_out.shape)

# print(np.average(esn_hybrid._w_out[:, -3:]))
# print(np.average(esn_hybrid._w_out[:, :-3]))

In [ ]:
# fig1 = plt.figure(figsize=(9, 6), dpi=300)
# ax1 = fig1.add_subplot(111, projection='3d')

# ax1.plot(y_test_normal[:, 0], y_test_normal[:, 1], y_test_normal[:, 2],
#         alpha=0.8, color='blue', label='simulation')
# ax1.plot(y_pred_normal[:, 0], y_pred_normal[:, 1], y_pred_normal[:, 2],
#         alpha=0.8, color='orange', label='pred normal')
# ax1.plot(y_pred_hybrid[:, 0], y_pred_hybrid[:, 1], y_pred_hybrid[:, 2],
#         alpha=0.8, color='red', label='pred hybrid')

# start = y_test_normal[0]
# ax1.plot([start[0]], [start[1]], [start[2]], 
#          color='black', linestyle='', marker='o', label='starting point')

# ax1.set_title("Simulation vs Prediction")
# ax1.set_xlabel('x')
# ax1.set_ylabel('y')
# ax1.set_zlabel('z')
# plt.legend()
# plt.show()

In [ ]:
# prediction_dict = {}

# y_test = None

# fig2 = plt.figure(figsize=(9, 6), dpi=300)
# ax2 = fig2.add_subplot(1, 1, 1)

# for name, prediction in prediction_dict.items():
#     rmse = rescomp.measures.rmse_over_time(time_series, y_test)
#     ax2.plot(rmse, linestyle='--', label=name)
#     print("AVG RMSE for " + name, np.average(rmse))

# ax2.set_title("RMSE")
# ax2.set_xlabel('time steps')
# ax2.set_ylabel('RMSE')
# plt.legend()
# plt.show()

In [ ]:
n_dim = 100
avg_deg = 3
p = 0.4 # largest eigenvalue (spectral radius)

esn1 = rescomp.esn.ESNWrapper()
esn1.create_network(n_dim = n_dim, n_rad=p, n_avg_deg=avg_deg, n_type_flag="erdos_renyi_directed")

esn2 = rescomp.esn.ESNWrapper()
esn2.create_network(n_dim = n_dim, n_rad=p, n_avg_deg=avg_deg, n_type_flag="erdos_renyi")


In [ ]:
print(np.argwhere(esn1._network).shape)
print("-----------------------------------------")
print(np.argwhere(esn2._network).shape)

In [ ]:
eps_list = np.linspace(0.004, 0.1, 25)
print(eps_list)

In [ ]:
r = np.ones((5, 5))*2
r = np.ones((5))*2

r_gen = np.copy(r)
r_gen.T[::2] = r.T[::2] ** 2

print(r, r_gen)